<h1>User defined parameters:</h1> The rest of the code runs dynamically without further user adjustment

In [50]:
# df name for processing
load_df_name = 'dream_data_raw.csv'
# Define text columns - user input
text_cols = ['Scene One','Scene Two','Scene Three','Scene Four']
# Define cluster range for slider. range(8:10) means 8 & 9, loses the last number
clusterRange = range(2,11)
# Text conversion choices
choices = {
           'use_sample_data':'Y',
           'sample_data_row_count':5000,
           'lemma':'Y',
           'lowercase':'Y',
           'uppercase':'N',
           'wordnet':'Y',
           'stemming':'N',
           'stopwords':'Y',
           'ngram_dup_remove_row':'Y',
           'remove_freq_infreq':'Y', # Min percent of times/docs depending on removal of dups in row
           'remove_too_freq':0.6, 
           'remove_count_infreq':5, 
           'remove_too_infreq':0.001, # Max percent of times/docs depending on removal of dups in row
           'minletterlen':3, # Set to 0 if not wanting to remove small words
           'ngramMin':2, # Set the floor for Ngram words, Ex. 2 will start at Bigrams
           'ngramMax':6, # Set ngramMax to 1 if wanting to use unigrams/tokens only
          }
# Models to run
model_choices = {'SpaCy_Vectors':'Y',
                 'LDA_Topics':'Y',}

<h1>Imports

In [51]:
import pandas as pd
import numpy as np
from collections import Counter
import spacy
from sklearn.cluster import KMeans
from sklearn.decomposition import PCA
import re
import plotly.offline as py
from plotly.offline import download_plotlyjs, init_notebook_mode, plot, iplot
import plotly.graph_objs as go
import nltk
from nltk import word_tokenize,sent_tokenize
from nltk.corpus import wordnet
from nltk.stem import PorterStemmer
from nltk.corpus import stopwords
from nltk.util import ngrams
import os
import pyLDAvis.gensim
import gensim        
from gensim import corpora
from gensim.models import LdaModel
pyLDAvis.enable_notebook()

In [52]:
nltk.download('wordnet')
nltk.download('punkt')

[nltk_data] Downloading package wordnet to
[nltk_data]     C:\Users\ryalott\AppData\Roaming\nltk_data...
[nltk_data]   Package wordnet is already up-to-date!
[nltk_data] Downloading package punkt to
[nltk_data]     C:\Users\ryalott\AppData\Roaming\nltk_data...
[nltk_data]   Package punkt is already up-to-date!


True

In [53]:
# Load SpaCy model. 'en_core_web_lg' is bigger than 'en' and has slight improvement
nlp = spacy.load('en')
init_notebook_mode(connected=True)

C:\Users\ryalott\AppData\Local\Continuum\anaconda3\lib\site-packages\msgpack_numpy.py:84: DeprecationWarning:

The binary mode of fromstring is deprecated, as it behaves surprisingly on unicode inputs. Use frombuffer instead

C:\Users\ryalott\AppData\Local\Continuum\anaconda3\lib\site-packages\msgpack_numpy.py:88: DeprecationWarning:

The binary mode of fromstring is deprecated, as it behaves surprisingly on unicode inputs. Use frombuffer instead

C:\Users\ryalott\AppData\Local\Continuum\anaconda3\lib\site-packages\msgpack_numpy.py:84: DeprecationWarning:

The binary mode of fromstring is deprecated, as it behaves surprisingly on unicode inputs. Use frombuffer instead

C:\Users\ryalott\AppData\Local\Continuum\anaconda3\lib\site-packages\msgpack_numpy.py:84: DeprecationWarning:

The binary mode of fromstring is deprecated, as it behaves surprisingly on unicode inputs. Use frombuffer instead

C:\Users\ryalott\AppData\Local\Continuum\anaconda3\lib\site-packages\msgpack_numpy.py:88: Deprec

C:\Users\ryalott\AppData\Local\Continuum\anaconda3\lib\site-packages\msgpack_numpy.py:84: DeprecationWarning:

The binary mode of fromstring is deprecated, as it behaves surprisingly on unicode inputs. Use frombuffer instead

C:\Users\ryalott\AppData\Local\Continuum\anaconda3\lib\site-packages\msgpack_numpy.py:88: DeprecationWarning:

The binary mode of fromstring is deprecated, as it behaves surprisingly on unicode inputs. Use frombuffer instead

C:\Users\ryalott\AppData\Local\Continuum\anaconda3\lib\site-packages\msgpack_numpy.py:84: DeprecationWarning:

The binary mode of fromstring is deprecated, as it behaves surprisingly on unicode inputs. Use frombuffer instead

C:\Users\ryalott\AppData\Local\Continuum\anaconda3\lib\site-packages\msgpack_numpy.py:84: DeprecationWarning:

The binary mode of fromstring is deprecated, as it behaves surprisingly on unicode inputs. Use frombuffer instead

C:\Users\ryalott\AppData\Local\Continuum\anaconda3\lib\site-packages\msgpack_numpy.py:88: Deprec

C:\Users\ryalott\AppData\Local\Continuum\anaconda3\lib\site-packages\msgpack_numpy.py:88: DeprecationWarning:

The binary mode of fromstring is deprecated, as it behaves surprisingly on unicode inputs. Use frombuffer instead

C:\Users\ryalott\AppData\Local\Continuum\anaconda3\lib\site-packages\msgpack_numpy.py:84: DeprecationWarning:

The binary mode of fromstring is deprecated, as it behaves surprisingly on unicode inputs. Use frombuffer instead

C:\Users\ryalott\AppData\Local\Continuum\anaconda3\lib\site-packages\msgpack_numpy.py:84: DeprecationWarning:

The binary mode of fromstring is deprecated, as it behaves surprisingly on unicode inputs. Use frombuffer instead

C:\Users\ryalott\AppData\Local\Continuum\anaconda3\lib\site-packages\msgpack_numpy.py:88: DeprecationWarning:

The binary mode of fromstring is deprecated, as it behaves surprisingly on unicode inputs. Use frombuffer instead

C:\Users\ryalott\AppData\Local\Continuum\anaconda3\lib\site-packages\msgpack_numpy.py:84: Deprec

C:\Users\ryalott\AppData\Local\Continuum\anaconda3\lib\site-packages\msgpack_numpy.py:84: DeprecationWarning:

The binary mode of fromstring is deprecated, as it behaves surprisingly on unicode inputs. Use frombuffer instead

C:\Users\ryalott\AppData\Local\Continuum\anaconda3\lib\site-packages\msgpack_numpy.py:84: DeprecationWarning:

The binary mode of fromstring is deprecated, as it behaves surprisingly on unicode inputs. Use frombuffer instead

C:\Users\ryalott\AppData\Local\Continuum\anaconda3\lib\site-packages\msgpack_numpy.py:84: DeprecationWarning:

The binary mode of fromstring is deprecated, as it behaves surprisingly on unicode inputs. Use frombuffer instead

C:\Users\ryalott\AppData\Local\Continuum\anaconda3\lib\site-packages\msgpack_numpy.py:88: DeprecationWarning:

The binary mode of fromstring is deprecated, as it behaves surprisingly on unicode inputs. Use frombuffer instead

C:\Users\ryalott\AppData\Local\Continuum\anaconda3\lib\site-packages\msgpack_numpy.py:84: Deprec

<h1>Dataframe loading and adjustments</h1>

In [54]:
# Load data
df = pd.read_csv('raw_dreams_dataset.csv', encoding='latin1').fillna('')
# Subsample
if choices['use_sample_data']=='Y':
    df = df.sample(min([len(df),choices['sample_data_row_count']]))
# Define original text column
df['text'] = df.apply(lambda x: ' '.join(x[text_cols]), axis=1)
# Create multiline blocks to represent original data on graphs
df['text_split'] = df.apply(lambda x: '<br>'.join([i.strip() for i in 
                   re.findall('.{0,100}[^ ]{0,10}', x['text'])][0:3]), axis=1)

In [55]:
def word_grams(words, min=1, max=4):
    """Get N grams. Source: 
       https://snippets.aktagon.com/snippets/619-how-to-generate-n-grams-with-python-and-nltk
    """
    s = []
    for n in range(min, max):
        for ngram in ngrams(words, n):
            s.append(' '.join(str(i) for i in ngram))
    return s

In [56]:
def cleanText(df,choices):
    """ Sets up the process flow for flowing between text processing options without degredation
        based on previous selections
    """
    if choices['lemma'] == 'Y':
        print('Lemmatizing')
        # SpaCy for part of speech lemmatzation, uses POS tagging
        docs = nlp.pipe(df['text'], batch_size=64, n_threads=6, disable=['ner'])
        # Runs lemma, lowercases as lemma default, and creates list of words in sents in texts
        processing = [sent_tokenize(' '.join([word.lemma_.lower() for word in text])) for text in docs]
        processing = [[word_tokenize(sent) for sent in text] for text in processing]
        # Adjusts to uppercase if user preferred
        if choices['uppercase'] == 'Y':
            print('Uppercasing')
            processing = [[[word.upper() for word in sent] for sent in text] for text in processing]
    # This block lower/upper/no processing instantiates word in sent in text list structure
    elif choices['lowercase'] == 'Y':
        print('Lowercasing')
        processing = df['text'].str.lower()
        processing = [[word_tokenize(sent) for sent in sent_tokenize(text)] for text in processing] 
    elif choices['uppercase'] == 'Y':
        print('Uppercasing')
        processing = df['text'].str.upper()
        processing = [[word_tokenize(sent) for sent in sent_tokenize(text)] for text in processing] 
    else: 
        print('No lemma or letter casing provided. Instantiating word in sent in text lists')
        processing = [sent_tokenize(text) for text in df['text']]
    if choices['wordnet'] == 'Y':
        print('Removing texts not in wordnet')
        processing = [[[word for word in sent if any(wordnet.synsets(word))] for sent in text] for text in processing]
    if choices['stopwords'] == 'Y':
        stop_words = set(stopwords.words('english'))
        processing = [[[word for word in sent if word.lower() not in stop_words] for sent in text] for text in processing]
    if choices['stemming'] == 'Y':
        print('Stemming')
        stemmer = PorterStemmer()
        processing = [[[stemmer.stem(word) for word in sent] for sent in text] for text in processing]
    if choices['minletterlen'] > 0:
        processing = [[[word for word in sent if len(word)>choices['minletterlen']] for sent in text] for text in processing]
    # Completed tokenization
    df['tokens'] = processing
    # Get Ngram words series
    # Set ngramMax to 1 if not wanting to use combinations, will simply flatten
    grams = [[word_grams(sent,choices['ngramMin'],choices['ngramMax']+1) for sent in text] for text in processing]
    processed_grams = []
    # Flatten lists to have words at the text level rather than sentence level
    for text in grams:
        flat_list = []
        for sent in text:
            for gram in sent:
                flat_list.append(gram)
        processed_grams.append(flat_list)
    if choices['ngram_dup_remove_row'] == 'Y':
        processed_grams = [list(set(a)) for a in processed_grams]
    if choices['remove_freq_infreq'] == 'Y':
        all_words = {word:0 for word in set([gram for text in processed_grams for gram in text])}
        for text in processed_grams:
            for ngram in text:
                all_words[ngram]+=1
        min_to_keep = max(choices['remove_too_infreq']*len(processed_grams),
                          choices['remove_count_infreq'])
        max_to_keep = choices['remove_too_freq']*len(processed_grams)
        
        keep_list = []
        for key in all_words.keys():
            if min_to_keep < all_words[key] < max_to_keep:
                keep_list.append(key)
        processed_grams = [list(set(keep_list).intersection(ngrams)) for ngrams in processed_grams]
    df['ngrams'] = processed_grams
    return df

Run text processing

In [57]:
df = cleanText(df,choices)

Lemmatizing
Removing texts not in wordnet


C:\Users\ryalott\AppData\Local\Continuum\anaconda3\lib\site-packages\ipykernel_launcher.py:7: DeprecationWarning:

generator 'ngrams' raised StopIteration

C:\Users\ryalott\AppData\Local\Continuum\anaconda3\lib\site-packages\ipykernel_launcher.py:7: DeprecationWarning:

generator 'ngrams' raised StopIteration

C:\Users\ryalott\AppData\Local\Continuum\anaconda3\lib\site-packages\ipykernel_launcher.py:7: DeprecationWarning:

generator 'ngrams' raised StopIteration

C:\Users\ryalott\AppData\Local\Continuum\anaconda3\lib\site-packages\ipykernel_launcher.py:7: DeprecationWarning:

generator 'ngrams' raised StopIteration

C:\Users\ryalott\AppData\Local\Continuum\anaconda3\lib\site-packages\ipykernel_launcher.py:7: DeprecationWarning:

generator 'ngrams' raised StopIteration

C:\Users\ryalott\AppData\Local\Continuum\anaconda3\lib\site-packages\ipykernel_launcher.py:7: DeprecationWarning:

generator 'ngrams' raised StopIteration

C:\Users\ryalott\AppData\Local\Continuum\anaconda3\lib\site-pack

C:\Users\ryalott\AppData\Local\Continuum\anaconda3\lib\site-packages\ipykernel_launcher.py:7: DeprecationWarning:

generator 'ngrams' raised StopIteration

C:\Users\ryalott\AppData\Local\Continuum\anaconda3\lib\site-packages\ipykernel_launcher.py:7: DeprecationWarning:

generator 'ngrams' raised StopIteration

C:\Users\ryalott\AppData\Local\Continuum\anaconda3\lib\site-packages\ipykernel_launcher.py:7: DeprecationWarning:

generator 'ngrams' raised StopIteration

C:\Users\ryalott\AppData\Local\Continuum\anaconda3\lib\site-packages\ipykernel_launcher.py:7: DeprecationWarning:

generator 'ngrams' raised StopIteration

C:\Users\ryalott\AppData\Local\Continuum\anaconda3\lib\site-packages\ipykernel_launcher.py:7: DeprecationWarning:

generator 'ngrams' raised StopIteration

C:\Users\ryalott\AppData\Local\Continuum\anaconda3\lib\site-packages\ipykernel_launcher.py:7: DeprecationWarning:

generator 'ngrams' raised StopIteration

C:\Users\ryalott\AppData\Local\Continuum\anaconda3\lib\site-pack

C:\Users\ryalott\AppData\Local\Continuum\anaconda3\lib\site-packages\ipykernel_launcher.py:7: DeprecationWarning:

generator 'ngrams' raised StopIteration

C:\Users\ryalott\AppData\Local\Continuum\anaconda3\lib\site-packages\ipykernel_launcher.py:7: DeprecationWarning:

generator 'ngrams' raised StopIteration

C:\Users\ryalott\AppData\Local\Continuum\anaconda3\lib\site-packages\ipykernel_launcher.py:7: DeprecationWarning:

generator 'ngrams' raised StopIteration

C:\Users\ryalott\AppData\Local\Continuum\anaconda3\lib\site-packages\ipykernel_launcher.py:7: DeprecationWarning:

generator 'ngrams' raised StopIteration

C:\Users\ryalott\AppData\Local\Continuum\anaconda3\lib\site-packages\ipykernel_launcher.py:7: DeprecationWarning:

generator 'ngrams' raised StopIteration

C:\Users\ryalott\AppData\Local\Continuum\anaconda3\lib\site-packages\ipykernel_launcher.py:7: DeprecationWarning:

generator 'ngrams' raised StopIteration

C:\Users\ryalott\AppData\Local\Continuum\anaconda3\lib\site-pack

C:\Users\ryalott\AppData\Local\Continuum\anaconda3\lib\site-packages\ipykernel_launcher.py:7: DeprecationWarning:

generator 'ngrams' raised StopIteration

C:\Users\ryalott\AppData\Local\Continuum\anaconda3\lib\site-packages\ipykernel_launcher.py:7: DeprecationWarning:

generator 'ngrams' raised StopIteration

C:\Users\ryalott\AppData\Local\Continuum\anaconda3\lib\site-packages\ipykernel_launcher.py:7: DeprecationWarning:

generator 'ngrams' raised StopIteration

C:\Users\ryalott\AppData\Local\Continuum\anaconda3\lib\site-packages\ipykernel_launcher.py:7: DeprecationWarning:

generator 'ngrams' raised StopIteration

C:\Users\ryalott\AppData\Local\Continuum\anaconda3\lib\site-packages\ipykernel_launcher.py:7: DeprecationWarning:

generator 'ngrams' raised StopIteration

C:\Users\ryalott\AppData\Local\Continuum\anaconda3\lib\site-packages\ipykernel_launcher.py:7: DeprecationWarning:

generator 'ngrams' raised StopIteration

C:\Users\ryalott\AppData\Local\Continuum\anaconda3\lib\site-pack

...

C:\Users\ryalott\AppData\Local\Continuum\anaconda3\lib\site-packages\ipykernel_launcher.py:7: DeprecationWarning:

generator 'ngrams' raised StopIteration

C:\Users\ryalott\AppData\Local\Continuum\anaconda3\lib\site-packages\ipykernel_launcher.py:7: DeprecationWarning:

generator 'ngrams' raised StopIteration

C:\Users\ryalott\AppData\Local\Continuum\anaconda3\lib\site-packages\ipykernel_launcher.py:7: DeprecationWarning:

generator 'ngrams' raised StopIteration

C:\Users\ryalott\AppData\Local\Continuum\anaconda3\lib\site-packages\ipykernel_launcher.py:7: DeprecationWarning:

generator 'ngrams' raised StopIteration

C:\Users\ryalott\AppData\Local\Continuum\anaconda3\lib\site-packages\ipykernel_launcher.py:7: DeprecationWarning:

generator 'ngrams' raised StopIteration

C:\Users\ryalott\AppData\Local\Continuum\anaconda3\lib\site-packages\ipykernel_launcher.py:7: DeprecationWarning:

generator 'ngrams' raised StopIteration

C:\Users\ryalott\AppData\Local\Continuum\anaconda3\lib\site-pack

C:\Users\ryalott\AppData\Local\Continuum\anaconda3\lib\site-packages\ipykernel_launcher.py:7: DeprecationWarning:

generator 'ngrams' raised StopIteration

C:\Users\ryalott\AppData\Local\Continuum\anaconda3\lib\site-packages\ipykernel_launcher.py:7: DeprecationWarning:

generator 'ngrams' raised StopIteration

C:\Users\ryalott\AppData\Local\Continuum\anaconda3\lib\site-packages\ipykernel_launcher.py:7: DeprecationWarning:

generator 'ngrams' raised StopIteration

C:\Users\ryalott\AppData\Local\Continuum\anaconda3\lib\site-packages\ipykernel_launcher.py:7: DeprecationWarning:

generator 'ngrams' raised StopIteration

C:\Users\ryalott\AppData\Local\Continuum\anaconda3\lib\site-packages\ipykernel_launcher.py:7: DeprecationWarning:

generator 'ngrams' raised StopIteration

C:\Users\ryalott\AppData\Local\Continuum\anaconda3\lib\site-packages\ipykernel_launcher.py:7: DeprecationWarning:

generator 'ngrams' raised StopIteration

C:\Users\ryalott\AppData\Local\Continuum\anaconda3\lib\site-pack

C:\Users\ryalott\AppData\Local\Continuum\anaconda3\lib\site-packages\ipykernel_launcher.py:7: DeprecationWarning:

generator 'ngrams' raised StopIteration

C:\Users\ryalott\AppData\Local\Continuum\anaconda3\lib\site-packages\ipykernel_launcher.py:7: DeprecationWarning:

generator 'ngrams' raised StopIteration

C:\Users\ryalott\AppData\Local\Continuum\anaconda3\lib\site-packages\ipykernel_launcher.py:7: DeprecationWarning:

generator 'ngrams' raised StopIteration

C:\Users\ryalott\AppData\Local\Continuum\anaconda3\lib\site-packages\ipykernel_launcher.py:7: DeprecationWarning:

generator 'ngrams' raised StopIteration

C:\Users\ryalott\AppData\Local\Continuum\anaconda3\lib\site-packages\ipykernel_launcher.py:7: DeprecationWarning:

generator 'ngrams' raised StopIteration

C:\Users\ryalott\AppData\Local\Continuum\anaconda3\lib\site-packages\ipykernel_launcher.py:7: DeprecationWarning:

generator 'ngrams' raised StopIteration

C:\Users\ryalott\AppData\Local\Continuum\anaconda3\lib\site-pack

C:\Users\ryalott\AppData\Local\Continuum\anaconda3\lib\site-packages\ipykernel_launcher.py:7: DeprecationWarning:

generator 'ngrams' raised StopIteration

C:\Users\ryalott\AppData\Local\Continuum\anaconda3\lib\site-packages\ipykernel_launcher.py:7: DeprecationWarning:

generator 'ngrams' raised StopIteration

C:\Users\ryalott\AppData\Local\Continuum\anaconda3\lib\site-packages\ipykernel_launcher.py:7: DeprecationWarning:

generator 'ngrams' raised StopIteration

C:\Users\ryalott\AppData\Local\Continuum\anaconda3\lib\site-packages\ipykernel_launcher.py:7: DeprecationWarning:

generator 'ngrams' raised StopIteration

C:\Users\ryalott\AppData\Local\Continuum\anaconda3\lib\site-packages\ipykernel_launcher.py:7: DeprecationWarning:

generator 'ngrams' raised StopIteration

C:\Users\ryalott\AppData\Local\Continuum\anaconda3\lib\site-packages\ipykernel_launcher.py:7: DeprecationWarning:

generator 'ngrams' raised StopIteration

C:\Users\ryalott\AppData\Local\Continuum\anaconda3\lib\site-pack

C:\Users\ryalott\AppData\Local\Continuum\anaconda3\lib\site-packages\ipykernel_launcher.py:7: DeprecationWarning:

generator 'ngrams' raised StopIteration

C:\Users\ryalott\AppData\Local\Continuum\anaconda3\lib\site-packages\ipykernel_launcher.py:7: DeprecationWarning:

generator 'ngrams' raised StopIteration

C:\Users\ryalott\AppData\Local\Continuum\anaconda3\lib\site-packages\ipykernel_launcher.py:7: DeprecationWarning:

generator 'ngrams' raised StopIteration

C:\Users\ryalott\AppData\Local\Continuum\anaconda3\lib\site-packages\ipykernel_launcher.py:7: DeprecationWarning:

generator 'ngrams' raised StopIteration

C:\Users\ryalott\AppData\Local\Continuum\anaconda3\lib\site-packages\ipykernel_launcher.py:7: DeprecationWarning:

generator 'ngrams' raised StopIteration

C:\Users\ryalott\AppData\Local\Continuum\anaconda3\lib\site-packages\ipykernel_launcher.py:7: DeprecationWarning:

generator 'ngrams' raised StopIteration

C:\Users\ryalott\AppData\Local\Continuum\anaconda3\lib\site-pack

<H1> Run SpaCy as requested

In [58]:
if model_choices['SpaCy_Vectors']=='Y':
    print('Vectorizing Text for SpaCy')
    df['vecs'] = [doc.vector for doc in nlp.pipe(df['text'],batch_size = 64,
              n_threads = 7)]
    # Format data
    vec_array = np.vstack(df['vecs'])
    # Do KMeans
    loss_scores = {}
    # Iterate on cluster range
    for i in clusterRange:
        kmean = KMeans(n_clusters=i,random_state=0).fit(vec_array)
        df['ClusterCount'+str(i)] = kmean.labels_
        loss_scores[i] = kmean.inertia_
        df['ClusterCount_3D'] = [list(i) for i in PCA(n_components=3,
                                           random_state=0).fit(vec_array)
                                           .transform(vec_array)]
        # Prepares data for 2D pca and visualization
        #df['ClusterCount'+str(i)+'_2D'] = [list(i) for i in PCA(n_components=2,
        #                                   random_state=0).fit(vec_array)
        #                                   .transform(vec_array)]
        display_df = pd.DataFrame(list(df['ClusterCount_3D']), columns = ['x','y','z'])
        trace0 = go.Scatter3d(
            x=display_df['x'],
            y=display_df['y'],
            z=display_df['z'],
            hoverinfo ='text',
            showlegend=False,
            text = ['Cluster: ' +str(row['ClusterCount'+str(i)])+'<br>'\
                    +row['text_split'] for index, row in df.iterrows()],
            marker=dict(
                size=2,
                cmax=i-1,
                cmin=0,
                color=df['ClusterCount'+str(i)],
                colorbar=dict(
                    title='Cluster Number',
                ),
                colorscale='Viridis'
            ),
            mode='markers'
        )
    
        layout = go.Layout(
            title = 'Clustering Using SpaCy Vectorization and PCA: '+str(i)+' Clusters',
            titlefont = dict(
                size = 20
            ),
            xaxis = dict(
                zeroline = False
            ),
            yaxis = dict(
                hoverformat = '.2f'
            )
        )
        data = [trace0]
        
        fig = go.Figure(data=data,layout=layout)
        
        py.plot(fig,filename='html/SpaCyVecClusters_'+str(i)+'.html')

Vectorizing Text for SpaCy


LDA Ref: <h5>http://shichaoji.com/tag/topic-modeling-python-lda-visualization-gensim-pyldavis-nltk/</h5>

In [ ]:
lda_out_models = []
if model_choices['LDA_Topics'] == 'Y':
    text_list = df.ngrams
    # Creating the term dictionary of our courpus, where every unique term is assigned an index.
    dictionary = corpora.Dictionary(text_list)
    dictionary.save('dictionary.dict')
    # Converting list of documents (corpus) into Document Term Matrix using dictionary prepared above.
    doc_term_matrix = [dictionary.doc2bow(doc) for doc in text_list]
    corpora.MmCorpus.serialize('corpus.mm', doc_term_matrix)
    # Loop on cluster range
    for i in clusterRange:
        # Creating the object for LDA model using gensim library
        Lda = gensim.models.ldamodel.LdaModel
        # Running and Trainign LDA model on the document term matrix.
        print('Running '+str(i)+' cluster LDA model')
        ldamodel = Lda(doc_term_matrix, num_topics=i, id2word = dictionary, passes=50)
        # save for later
        ldamodel.save('topic.model')
        # reopen model
        loading = LdaModel.load('topic.model')
        
        pyLDAvis.enable_notebook()
        
        d = gensim.corpora.Dictionary.load('dictionary.dict')
        c = gensim.corpora.MmCorpus('corpus.mm')
        lda = gensim.models.LdaModel.load('topic.model')
        
        lda_out = pyLDAvis.gensim.prepare(lda, c, d)
        pyLDAvis.enable_notebook()
        lda_out_models.append(lda_out)
        
        topics = ldamodel.print_topics(num_words=10)
        terms = ['Topic: '+str(topic[0])+'<br>'+'Top Terms: '+' | '.join(
                re.findall('\"([^\"]*)\"',topic[1])) for topic in topics]
        trace0 = go.Scatter(
            x=lda_out[0]['x'],
            y=lda_out[0]['y'],
            hoverinfo ='text',
            showlegend=False,
            text = terms,
            marker=dict(
                size=lda_out[0]['Freq']*5,
                cmax=i-1,
                cmin=0,
                color=lda_out[0]['topics']-1,
                colorbar=dict(
                    title='Cluster Number',
                ),
                line = dict(
                  color = 'rgb(0, 0, 0)',
                  width = 2
                ),
                colorscale='Viridis'
            ),
            mode='markers'
        )
        
        layout = go.Layout(
            title = 'Clustering LDA: '+str(i),
            titlefont = dict(
                size = 20
            )
        )
        data = [trace0]
        
        fig = go.Figure(data=data,layout=layout)
        
        py.plot(fig,filename='html/LDA_Clusters_'+str(i)+'.html')
        

Running 2 cluster LDA model


<h1> Jupyter in-line visualization</h1> 
would eventually be replaced with saveable/shareable/witesite hostable visualizations like those written in Plotly above

In [46]:
lda_out_models[2]

PreparedData(topic_coordinates=              x         y  topics  cluster       Freq
topic                                                
1      0.291953  0.024155       1        1  38.284508
0      0.102219  0.114632       2        1  22.816311
2     -0.112189 -0.341036       3        1  20.165754
3     -0.281982  0.202248       4        1  18.733425, topic_info=     Category         Freq                  Term        Total  loglift  \
term                                                                     
46    Default  5455.000000            last night  5455.000000  30.0000   
52    Default  3357.000000            dream last  3357.000000  29.0000   
53    Default  2988.000000      dream last night  2988.000000  28.0000   
155   Default  2107.000000           night dream  2107.000000  27.0000   
154   Default  1601.000000      last night dream  1601.000000  26.0000   
8     Default  3773.000000             look like  3773.000000  25.0000   
546   Default  1256.000000            dream mean  1256.000000  24.0000   
1631  Default  1075.000000       interpret dream  1075.000000  23.0000   
87    Default  2003.000000             real life  2003.000000  22.0000   
1520  Default  1509.000000           please help  1509.000000  21.0000   
1872  Default   791.000000        help interpret   791.000000  20.0000   
1341  Default   756.000000            know dream   756.000000  19.0000   
1445  Default   755.000000            help dream   755.000000  18.0000   
1547  Default   716.000000         morning dream   716.000000  17.0000   
317   Default   961.000000             know mean   961.000000  16.0000   
1429  Default   616.000000            keep dream   616.000000  15.0000   
163   Default   897.000000           holy spirit   897.000000  14.0000   
2     Default  1688.000000             come back  1688.000000  13.0000   
1622  Default   898.000000            mean dream   898.000000  12.0000   
2390  Default   542.000000          please check   542.000000  11.0000   
341   Default   534.000000            time dream   534.000000  10.0000   
1890  Default   495.000000      please interpret   495.000000   9.0000   
607   Default   510.000000            first time   510.000000   8.0000   
527   Default   506.000000            back sleep   506.000000   7.0000   
391   Default   536.000000          someone tell   536.000000   6.0000   
1463  Default   529.000000       help understand   529.000000   5.0000   
1518  Default   785.000000          good morning   785.000000   4.0000   
1085  Default   783.000000             need help   783.000000   3.0000   
202   Default   785.000000            dream walk   785.000000   2.0000   
2391  Default   466.000000       private message   466.000000   1.0000   
...       ...          ...                   ...          ...      ...   
1922   Topic4   223.090775         insight dream   223.892807   1.6713   
1640   Topic4   224.208771             feel real   225.019440   1.6713   
1693   Topic4   220.674576  dream interpretation   221.480042   1.6712   
1634   Topic4   214.544144           wonder mean   215.351395   1.6711   
528    Topic4   213.892410             fall back   214.716904   1.6710   
1649   Topic4   182.916641           white dress   183.725647   1.6704   
1609   Topic4   180.231812             also like   181.035767   1.6704   
2179   Topic4   173.427048          give insight   174.218887   1.6703   
1478   Topic4   175.328613             lord show   176.138153   1.6703   
1461   Topic4   174.293381           dream today   175.100845   1.6702   
1323   Topic4   182.801544         someone house   183.649719   1.6702   
522    Topic4   172.097351          look forward   172.901169   1.6702   
1559   Topic4   167.027039   need interpretation   167.821777   1.6701   
1434   Topic4   165.768021            dream move   166.573349   1.6700   
1639   Topic4   163.094254            dream pray   163.893265   1.6700   
1384   Topic4   165.578064             tell back   166.441299   1.6697   
46     